In [1]:
%cd ..

D:\plum_music


In [2]:
import pickle
from pathlib import Path

from config.config import get_constants_dict
from models.processing import get_encoding_for_genre
from utils.magenta_midi_utils import save_midi
from utils.magenta_models_utils import get_model
from utils.magenta_note_seq_utils import get_sec_for_num_bars
from utils.data_utils import get_all_songs_from_genres_of_size
from utils.lakh_utils import get_midi_path, get_matched_midi_md5, get_msd_score_matches
from utils.msd_utils import get_artist

import pandas as pd
import numpy as np
import plotly.express as px
from sklearn.manifold import TSNE

import note_seq as ns
from magenta.models.music_vae.trained_model import NoExtractedExamplesError, MultipleExtractedExamplesError

In [3]:
def load_encodings(genre="all"):        
    encodings_path = Path(constants["DATA_PATH"], "encodings")
    if genre == "all":
        encodings_files = list(encodings_path.glob("*.pkl"))
    else:
        encodings_files = list(encodings_path.glob(f"*{genre}*.pkl"))
        
    genre_labels, encodings, msd_ids = [], [], []
    for file in encodings_files:
        with file.open('rb') as f:
            if "genre" in file.stem:
                genre_labels.extend(pickle.load(f))
            elif "encoding" in file.stem:
                encodings.extend(pickle.load(f))
            elif "msd" in file.stem:
                msd_ids.extend(pickle.load(f))

    assert len(genre_labels) == len(encodings) == len(msd_ids)
    return genre_labels, encodings, msd_ids

        
def play_msd(msd_id):
    return ns.play_sequence(
        ns.midi_file_to_note_sequence(
            get_midi_path(
                msd_id,
                get_matched_midi_md5(msd_id, get_msd_score_matches())
            )
        )
    )


def tsne_embedd(
    encodings_arr,
    n_components=2,
    perplexity=30,
    early_exaggeration=12.0,
    learning_rate=200.0,
    n_iter=1000,
    n_iter_without_progress=300,
    metric='euclidean',
    init='random',
    random_state=42
):
    if isinstance(encodings_arr, list):
        enc = np.vstack(encodings_arr)
    else:
        enc = encodings_arr
        
    return TSNE(
    n_components=n_components,
    perplexity=perplexity,
    early_exaggeration=early_exaggeration,
    learning_rate=learning_rate,
    n_iter=n_iter,
    n_iter_without_progress=n_iter_without_progress,
    metric=metric,
    init=init,
    random_state=random_state
).fit_transform(enc)
    
    
def plot_embedding(embedded, labels, ids, df=None):
    if not df:
        df = pd.read_csv(constants["LMD_METADATA_CSV_FILE"])
        df = df[df.msdID.isin(ids)]
        
    if embedded.shape[1] == 2:
        return px.scatter(
            data_frame=df,
            x=embedded[:,0],
            y=embedded[:,1],
            color=labels,
            hover_name=ids,
            hover_data=["artist", "track"],
            labels={"color": "genre"}
        )
    elif embedded.shape[1] == 3:
        return px.scatter_3d(
            data_frame=df,
            x=embedded[:,0],
            y=embedded[:,1],
            z=embedded[:,2],
            color=labels,
            hover_name=ids,
            hover_data=["artist", "track"],
            labels={"color": "genre"}
        )
    else:
        pass
      

In [4]:
constants = get_constants_dict()
meta = pd.read_csv(constants["LMD_METADATA_CSV_FILE"])

## Latent Space

In [5]:
model = get_model(constants["NAME_MUSICVAE_MULTITRACK"])

--- Logging error ---
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 1025, in emit
    msg = self.format(record)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 869, in format
    return fmt.format(record)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 611, in format
    s = self.formatMessage(record)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 580, in formatMessage
    return self._style.format(record)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 422, in format
    return self._fmt % record.__dict__
KeyError: 'messages'
Call stack:
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\runpy.py", line 193, in _run_module_as_main
    "__main__", mod_spec)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\runpy.py", line 85, in _run_code
    exec(code, run_globals)
  File "C:\ProgramDa

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: module 'gast' has no attribute 'Index'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert


--- Logging error ---
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\site-packages\tensorflow\python\autograph\impl\api.py", line 584, in converted_call
    converted_f = conversion.convert(target_entity, program_ctx)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\site-packages\tensorflow\python\autograph\impl\conversion.py", line 119, in convert
    entity, program_ctx.options, program_ctx, custom_vars)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\site-packages\tensorflow\python\autograph\pyct\transpiler.py", line 412, in transform_function
    extra_locals)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\site-packages\tensorflow\python\autograph\pyct\transpiler.py", line 373, in _transformed_factory
    nodes, ctx = self._transform_function(fn, user_context)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\site-packages\tensorflow\python\autograph\pyct\transpiler.py", line 339, in _transform_function
    node = self.tran

--- Logging error ---
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 1025, in emit
    msg = self.format(record)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 869, in format
    return fmt.format(record)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 611, in format
    s = self.formatMessage(record)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 580, in formatMessage
    return self._style.format(record)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 422, in format
    return self._fmt % record.__dict__
KeyError: 'messages'
Call stack:
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\runpy.py", line 193, in _run_module_as_main
    "__main__", mod_spec)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\runpy.py", line 85, in _run_code
    exec(code, run_globals)
  File "C:\ProgramDa

--- Logging error ---
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 1025, in emit
    msg = self.format(record)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 869, in format
    return fmt.format(record)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 611, in format
    s = self.formatMessage(record)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 580, in formatMessage
    return self._style.format(record)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\logging\__init__.py", line 422, in format
    return self._fmt % record.__dict__
KeyError: 'messages'
Call stack:
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\runpy.py", line 193, in _run_module_as_main
    "__main__", mod_spec)
  File "C:\ProgramData\Anaconda3\envs\plum_music\lib\runpy.py", line 85, in _run_code
    exec(code, run_globals)
  File "C:\ProgramDa

## Load data

In [ ]:
hh_g, hh_e, hh_m = load_encodings("hip hop rnb and dance hall")
country_g, country_e, country_m = load_encodings("country")

## Splitting

In [ ]:
for bla in country_m:
    s = ns.midi_file_to_note_sequence(
        get_midi_path(bla, get_matched_midi_md5(bla, get_msd_score_matches()))
    )
    pm = ns.sequence_proto_to_pretty_midi(s)
    if len(pm.instruments) <= 8:
        print(meta[meta.msdID == bla].loc[:, ["msdID", "artist", "track"]])
        ns.play_sequence(s, synth=ns.fluidsynth)

In [ ]:
hh1 = "TRZDMWV128E0796976"
hh2 = "TRKWKER128F1482409"
hh3 = "TRYFUNE12903CCDCD5"

In [ ]:
c1 = "TRULTSR12903CBD13D"
c2 = "TRCRKXS12903CD21F9"
c3 = "TRQHQLN12903CBD237"

In [ ]:
c = ns.midi_file_to_note_sequence(
    get_midi_path(c2, get_matched_midi_md5(c2, get_msd_score_matches()))
)

In [ ]:
splits = ns.split_note_sequence(
    c,
    get_sec_for_num_bars(c, n_bars=1)
)

## Encoding

In [ ]:
encs = []
for split in splits:
    try:
        encs.append(model.encode([split]))
    except NoExtractedExamplesError:
        encs.append(split)
        continue

In [ ]:
[type(e) for e in encs]

## Decoding

In [ ]:
decs = []
for enc in encs:
    try:
        decs.append(model.decode([enc]))
    except NoExtractedExamplesError:
        decs.append(enc)

In [ ]:
ns.play_sequence(decs[0], synth=ns.fluidsynth)

## Largest MIDI dataset

In [6]:
largest_path = Path(constants["DATA_PATH"], "largest_midi", "130000_Pop_Rock_Classical_Videogame_EDM_MIDI_Archive[6_19_15]")

In [7]:
path1 = largest_path / "AMERICANA_FOLK_www.pdmusic.org_MIDIRip" / "folk" / "Norfolk_Gals.mid"
ns1 = ns.midi_file_to_note_sequence(str(path1))

In [8]:
encs = {}
num_files = 0
num_skipped = 0
#folder = largest_path / "AMERICANA_FOLK_www.pdmusic.org_MIDIRip" / "1800s"
folder = Path(constants["DATA_PATH"], "google_samples")

In [12]:
for p in folder.glob('*.mid'):
    num_files += 1
    s = ns.midi_file_to_note_sequence(str(p))
    try:
        e = model.encode([s])
    except (NoExtractedExamplesError, MultipleExtractedExamplesError) as e:
        num_skipped += 1
        continue
    except Exception:
        continue
    else:
        encs[p.stem] = e
        
print(f"Found {num_files} files")
print(f"Encoded {len(encs)} files")
print(f"Skipped {num_skipped} files")

Found 5 files
Encoded 4 files
Skipped 1 files


In [13]:
encs.keys()

dict_keys(['dance', 'metal', 'strings', 'winds'])

In [23]:
start = ns.midi_file_to_note_sequence(str(folder / "metal.mid"))
end = ns.midi_file_to_note_sequence(str(folder / "dance.mid"))
i = model.interpolate(start, end, 32, temperature=1.5)

In [17]:
ns.plot_sequence(ns.concatenate_sequences(i))
ns.play_sequence(ns.concatenate_sequences(i))

Loading BokehJS ...

In [24]:
save_midi([ns.concatenate_sequences(i)])

Generated midi file: D:\plum_music\data\sequence_00_2020-09-19_182750.mid


In [35]:
pm = ns.sequence_proto_to_pretty_midi(start)

In [40]:
vars(pm.instruments[0])

{'program': 30,
 'is_drum': False,
 'name': '',
 'notes': [Note(start=0.000000, end=0.196546, pitch=57, velocity=110),
  Note(start=0.000000, end=0.196546, pitch=64, velocity=110),
  Note(start=0.197369, end=0.393915, pitch=52, velocity=110),
  Note(start=0.394737, end=0.591283, pitch=52, velocity=110),
  Note(start=0.592105, end=0.788652, pitch=52, velocity=110),
  Note(start=0.789474, end=0.986020, pitch=52, velocity=110),
  Note(start=0.986843, end=1.183389, pitch=52, velocity=110),
  Note(start=1.184211, end=1.380757, pitch=52, velocity=110),
  Note(start=1.381579, end=1.578126, pitch=52, velocity=110)],
 'pitch_bends': [],
 'control_changes': [ControlChange(number=121, value=0, time=0.000000),
  ControlChange(number=7, value=100, time=0.000000),
  ControlChange(number=10, value=64, time=0.000000),
  ControlChange(number=91, value=0, time=0.000000),
  ControlChange(number=93, value=0, time=0.000000)]}

In [42]:
start

ticks_per_quarter: 480
time_signatures {
  numerator: 4
  denominator: 4
}
key_signatures {
}
tempos {
  qpm: 151.99993920002433
}
notes {
  pitch: 57
  velocity: 110
  end_time: 0.19654613125
  program: 30
}
notes {
  pitch: 64
  velocity: 110
  end_time: 0.19654613125
  program: 30
}
notes {
  pitch: 52
  velocity: 110
  start_time: 0.1973685
  end_time: 0.39391463125
  program: 30
}
notes {
  pitch: 52
  velocity: 110
  start_time: 0.394737
  end_time: 0.59128313125
  program: 30
}
notes {
  pitch: 52
  velocity: 110
  start_time: 0.5921055
  end_time: 0.78865163125
  program: 30
}
notes {
  pitch: 52
  velocity: 110
  start_time: 0.789474
  end_time: 0.98602013125
  program: 30
}
notes {
  pitch: 52
  velocity: 110
  start_time: 0.9868425000000001
  end_time: 1.18338863125
  program: 30
}
notes {
  pitch: 52
  velocity: 110
  start_time: 1.184211
  end_time: 1.38075713125
  program: 30
}
notes {
  pitch: 52
  velocity: 110
  start_time: 1.3815795
  end_time: 1.57812563125
  program